# CIS7030 - Geospatial Analysis 
### Module Leader   : Dr Angesh Anupam
### Workshop Tutor : Dr Ali Shahaab

# PART 2 – Geospatial Sentiment Analysis using Social Media Data

## Task 2.1: Data pre-processing

In [1]:
import geopandas as gpd
import pandas as pd 
import matplotlib.pyplot as mpl
import seaborn as sns
import plotly.express as pye
import plotly.graph_objects as go
from textblob import TextBlob #to ind the polarity and subjectivity of the tweet
import sys,tweepy # to gather the tweets
from wordcloud import WordCloud # to produce word cloud
import numpy as np
import re # library to clean the tweets
import folium

In [2]:
tweet_data = pd.read_csv('https://raw.githubusercontent.com/saikumarsandra/Cis7030/main/tweet.csv')

In [3]:
tweet_data

created_at      tweet_id  \
0    15/10/2020 00:00  1.320000e+18   
1    15/10/2020 00:00  1.320000e+18   
2    15/10/2020 00:00  1.320000e+18   
3    15/10/2020 00:00  1.320000e+18   
4    15/10/2020 00:00  1.320000e+18   
..                ...           ...   
495  15/10/2020 00:29  1.320000e+18   
496  15/10/2020 00:29  1.320000e+18   
497  15/10/2020 00:29  1.320000e+18   
498  15/10/2020 00:29  1.320000e+18   
499  15/10/2020 00:29  1.320000e+18   

                                                 tweet  likes  retweet_count  \
0    #Elecciones2020 | En #Florida: #JoeBiden dice ...      0              0   
1    #HunterBiden #HunterBidenEmails #JoeBiden #Joe...      0              0   
2    @IslandGirlPRV @BradBeauregardJ @MeidasTouch T...      0              0   
3    @chrislongview Watching and setting dvr. Let‚Ä...      0              0   
4    #censorship #HunterBiden #Biden #BidenEmails #...      1              0   
..                                                 ...    ...            ...   
495  Must watchüëáüèª#Biden family corruption. ht...     35             32   
496  FACTS: @JoeBiden has been accused of sexual as...     16             10   
497  Hunter #Biden won a Nobel Peace Prize, R's try...      0              0   
498  This is utter bullshit. This was a news articl...      4              0   
499  Does the #HunterBiden #HunterBidenEmails #NYPo...      0              0   

                 source       user_id           user_name user_screen_name  \
0             TweetDeck  3.606665e+08  El Sol Latino News  elsollatinonews   
1      Twitter for iPad  8.099044e+08   Cheri A. üá∫üá∏     Biloximeemaw   
2       Twitter Web App  3.494182e+09          Flag Waver      Flag_Wavers   
3    Twitter for iPhone  8.240000e+17       Michelle Ferg    MichelleFerg4   
4       Twitter Web App  1.030000e+18      the Gold State    theegoldstate   
..                  ...           ...                 ...              ...   
495  Twitter for iPhone  3.031552e+07          Susan Ward    Susaninlaguna   
496     Twitter Web App  8.256080e+08   Justin T. Haskins   JustinTHaskins   
497     Twitter Web App  9.470000e+17      Nicholas Sones        NickSones   
498  Twitter for iPhone  7.749858e+08              kaytee    TeamDaniMBB14   
499  Twitter for iPhone  1.290000e+18      @realateachick    realateachick   

                                      user_description  ...  \
0    üåê Noticias de inter√©s para latinos de la c...  ...   
1    Locked and loaded Meemaw. Love God, my family ...  ...   
2                                                  NaN  ...   
3                                                  NaN  ...   
4    A Silicon Valley #independent #News #Media #St...  ...   
..                                                 ...  ...   
495  Amazon Bestselling Author. Believes in family ...  ...   
496  Christian. Conservative Millennial. Editorial ...  ...   
497        Fight Back Harder! Publisher of @GLRepublic  ...   
498  Names Kaytee. 1st Official fan account for the...  ...   
499        Reality TV nonsense and nonsense in general  ...   

    user_followers_count                 user_location        lat        long  \
0                   1860  Philadelphia, PA / Miami, FL  25.774270  -80.193660   
1                   6628                           NaN        NaN         NaN   
2                   1536         Golden Valley Arizona  46.304036 -109.171431   
3                     27                           NaN        NaN         NaN   
4                    390               California, USA  36.701463 -118.755997   
..                   ...                           ...        ...         ...   
495                26012                           NaN        NaN         NaN   
496                18940                The South, USA  36.638392  127.696119   
497                 2183    Silver Spring Township, PA  41.299538  -74.848779   
498                  294                           NaN        NaN         NaN

In [4]:
tweet_data.isnull().sum()

created_at                0
tweet_id                  0
tweet                     0
likes                     0
retweet_count             0
source                    1
user_id                   0
user_name                 0
user_screen_name          0
user_description         83
user_join_date            0
user_followers_count      0
user_location           200
lat                     283
long                    283
city                    408
country                 283
continent               283
state                   330
state_code              337
collected_at              0
dtype: int64

## Cleaning the tweets

In [5]:
def clean_the_tweets(txt):
    txt = re.sub(r'@[A-Za-z0-9_]+', '', txt)  # Remove @mentions
    txt = re.sub(r'#', '', txt)# Remove hashtags#
    txt = re.sub(r'RT : ', '', txt)# Remove retweets:
    txt = re.sub(r'https?:\/\/[A-Za-z0-9\.\/]+', '', txt)# Remove urls
    return txt
tweet_data['tweet'] = tweet_data['tweet'].apply(clean_the_tweets)
tweet_data

created_at      tweet_id  \
0    15/10/2020 00:00  1.320000e+18   
1    15/10/2020 00:00  1.320000e+18   
2    15/10/2020 00:00  1.320000e+18   
3    15/10/2020 00:00  1.320000e+18   
4    15/10/2020 00:00  1.320000e+18   
..                ...           ...   
495  15/10/2020 00:29  1.320000e+18   
496  15/10/2020 00:29  1.320000e+18   
497  15/10/2020 00:29  1.320000e+18   
498  15/10/2020 00:29  1.320000e+18   
499  15/10/2020 00:29  1.320000e+18   

                                                 tweet  likes  retweet_count  \
0    Elecciones2020 | En Florida: JoeBiden dice que...      0              0   
1    HunterBiden HunterBidenEmails JoeBiden JoeBide...      0              0   
2       This is how Biden made his ! TrumpIsNotAmer...      0              0   
3     Watching and setting dvr. Let‚Äôs give him bo...      0              0   
4    censorship HunterBiden Biden BidenEmails Biden...      1              0   
..                                                 ...    ...            ...   
495        Must watchüëáüèªBiden family corruption.      35             32   
496  FACTS:  has been accused of sexual assault, ma...     16             10   
497  Hunter Biden won a Nobel Peace Prize, R's try ...      0              0   
498  This is utter bullshit. This was a news articl...      4              0   
499  Does the HunterBiden HunterBidenEmails NYPost ...      0              0   

                 source       user_id           user_name user_screen_name  \
0             TweetDeck  3.606665e+08  El Sol Latino News  elsollatinonews   
1      Twitter for iPad  8.099044e+08   Cheri A. üá∫üá∏     Biloximeemaw   
2       Twitter Web App  3.494182e+09          Flag Waver      Flag_Wavers   
3    Twitter for iPhone  8.240000e+17       Michelle Ferg    MichelleFerg4   
4       Twitter Web App  1.030000e+18      the Gold State    theegoldstate   
..                  ...           ...                 ...              ...   
495  Twitter for iPhone  3.031552e+07          Susan Ward    Susaninlaguna   
496     Twitter Web App  8.256080e+08   Justin T. Haskins   JustinTHaskins   
497     Twitter Web App  9.470000e+17      Nicholas Sones        NickSones   
498  Twitter for iPhone  7.749858e+08              kaytee    TeamDaniMBB14   
499  Twitter for iPhone  1.290000e+18      @realateachick    realateachick   

                                      user_description  ...  \
0    üåê Noticias de inter√©s para latinos de la c...  ...   
1    Locked and loaded Meemaw. Love God, my family ...  ...   
2                                                  NaN  ...   
3                                                  NaN  ...   
4    A Silicon Valley #independent #News #Media #St...  ...   
..                                                 ...  ...   
495  Amazon Bestselling Author. Believes in family ...  ...   
496  Christian. Conservative Millennial. Editorial ...  ...   
497        Fight Back Harder! Publisher of @GLRepublic  ...   
498  Names Kaytee. 1st Official fan account for the...  ...   
499        Reality TV nonsense and nonsense in general  ...   

    user_followers_count                 user_location        lat        long  \
0                   1860  Philadelphia, PA / Miami, FL  25.774270  -80.193660   
1                   6628                           NaN        NaN         NaN   
2                   1536         Golden Valley Arizona  46.304036 -109.171431   
3                     27                           NaN        NaN         NaN   
4                    390               California, USA  36.701463 -118.755997   
..                   ...                           ...        ...         ...   
495                26012                           NaN        NaN         NaN   
496                18940                The South, USA  36.638392  127.696119   
497                 2183    Silver Spring Township, PA  41.299538  -74.848779   
498                  294                           NaN        NaN         NaN

# Task 2.2: Polarity analysis

In [6]:
def Polarity_score(txt):
    return TextBlob(txt).sentiment.polarity
tweet_data['Polarity_score'] = tweet_data['tweet'].apply(Polarity_score)
tweet_data.head()

created_at      tweet_id  \
0  15/10/2020 00:00  1.320000e+18   
1  15/10/2020 00:00  1.320000e+18   
2  15/10/2020 00:00  1.320000e+18   
3  15/10/2020 00:00  1.320000e+18   
4  15/10/2020 00:00  1.320000e+18   

                                               tweet  likes  retweet_count  \
0  Elecciones2020 | En Florida: JoeBiden dice que...      0              0   
1  HunterBiden HunterBidenEmails JoeBiden JoeBide...      0              0   
2     This is how Biden made his ! TrumpIsNotAmer...      0              0   
3   Watching and setting dvr. Let‚Äôs give him bo...      0              0   
4  censorship HunterBiden Biden BidenEmails Biden...      1              0   

               source       user_id           user_name user_screen_name  \
0           TweetDeck  3.606665e+08  El Sol Latino News  elsollatinonews   
1    Twitter for iPad  8.099044e+08   Cheri A. üá∫üá∏     Biloximeemaw   
2     Twitter Web App  3.494182e+09          Flag Waver      Flag_Wavers   
3  Twitter for iPhone  8.240000e+17       Michelle Ferg    MichelleFerg4   
4     Twitter Web App  1.030000e+18      the Gold State    theegoldstate   

                                    user_description  ...  \
0  üåê Noticias de inter√©s para latinos de la c...  ...   
1  Locked and loaded Meemaw. Love God, my family ...  ...   
2                                                NaN  ...   
3                                                NaN  ...   
4  A Silicon Valley #independent #News #Media #St...  ...   

                  user_location        lat        long  city  \
0  Philadelphia, PA / Miami, FL  25.774270  -80.193660   NaN   
1                           NaN        NaN         NaN   NaN   
2         Golden Valley Arizona  46.304036 -109.171431   NaN   
3                           NaN        NaN         NaN   NaN   
4               California, USA  36.701463 -118.755997   NaN   

                    country      continent       state state_code  \
0  United States of America  North America     Florida         FL   
1                       NaN            NaN         NaN        NaN   
2  United States of America  North America     Montana         MT   
3                       NaN            NaN         NaN        NaN   
4  United States of America  North America  California         CA   

       collected_at Polarity_score  
0  21/10/2020 00:00            0.0  
1           00:00.5            0.0  
2           00:01.0            0.0  
3           00:01.6            0.0  
4           00:02.1            0.0  

[5 rows x 22 columns]

### calculating the sentiment of polarity

In [7]:
def sentiment(score):
    if score<0:
        return "negative"
    elif score==0:
        return "neutral"
    elif score>0 :
        return "positive"
tweet_data['Sentiment']=tweet_data['Polarity_score'].apply(sentiment)
tweet_data.head()

created_at      tweet_id  \
0  15/10/2020 00:00  1.320000e+18   
1  15/10/2020 00:00  1.320000e+18   
2  15/10/2020 00:00  1.320000e+18   
3  15/10/2020 00:00  1.320000e+18   
4  15/10/2020 00:00  1.320000e+18   

                                               tweet  likes  retweet_count  \
0  Elecciones2020 | En Florida: JoeBiden dice que...      0              0   
1  HunterBiden HunterBidenEmails JoeBiden JoeBide...      0              0   
2     This is how Biden made his ! TrumpIsNotAmer...      0              0   
3   Watching and setting dvr. Let‚Äôs give him bo...      0              0   
4  censorship HunterBiden Biden BidenEmails Biden...      1              0   

               source       user_id           user_name user_screen_name  \
0           TweetDeck  3.606665e+08  El Sol Latino News  elsollatinonews   
1    Twitter for iPad  8.099044e+08   Cheri A. üá∫üá∏     Biloximeemaw   
2     Twitter Web App  3.494182e+09          Flag Waver      Flag_Wavers   
3  Twitter for iPhone  8.240000e+17       Michelle Ferg    MichelleFerg4   
4     Twitter Web App  1.030000e+18      the Gold State    theegoldstate   

                                    user_description  ...        lat  \
0  üåê Noticias de inter√©s para latinos de la c...  ...  25.774270   
1  Locked and loaded Meemaw. Love God, my family ...  ...        NaN   
2                                                NaN  ...  46.304036   
3                                                NaN  ...        NaN   
4  A Silicon Valley #independent #News #Media #St...  ...  36.701463   

         long city                   country      continent       state  \
0  -80.193660  NaN  United States of America  North America     Florida   
1         NaN  NaN                       NaN            NaN         NaN   
2 -109.171431  NaN  United States of America  North America     Montana   
3         NaN  NaN                       NaN            NaN         NaN   
4 -118.755997  NaN  United States of America  North America  California   

  state_code      collected_at Polarity_score Sentiment  
0         FL  21/10/2020 00:00            0.0   neutral  
1        NaN           00:00.5            0.0   neutral  
2         MT           00:01.0            0.0   neutral  
3        NaN           00:01.6            0.0   neutral  
4         CA           00:02.1            0.0   neutral  

[5 rows x 23 columns]

In [8]:
tweet_data = tweet_data.fillna(method='ffill')
tweet_data

created_at      tweet_id  \
0    15/10/2020 00:00  1.320000e+18   
1    15/10/2020 00:00  1.320000e+18   
2    15/10/2020 00:00  1.320000e+18   
3    15/10/2020 00:00  1.320000e+18   
4    15/10/2020 00:00  1.320000e+18   
..                ...           ...   
495  15/10/2020 00:29  1.320000e+18   
496  15/10/2020 00:29  1.320000e+18   
497  15/10/2020 00:29  1.320000e+18   
498  15/10/2020 00:29  1.320000e+18   
499  15/10/2020 00:29  1.320000e+18   

                                                 tweet  likes  retweet_count  \
0    Elecciones2020 | En Florida: JoeBiden dice que...      0              0   
1    HunterBiden HunterBidenEmails JoeBiden JoeBide...      0              0   
2       This is how Biden made his ! TrumpIsNotAmer...      0              0   
3     Watching and setting dvr. Let‚Äôs give him bo...      0              0   
4    censorship HunterBiden Biden BidenEmails Biden...      1              0   
..                                                 ...    ...            ...   
495        Must watchüëáüèªBiden family corruption.      35             32   
496  FACTS:  has been accused of sexual assault, ma...     16             10   
497  Hunter Biden won a Nobel Peace Prize, R's try ...      0              0   
498  This is utter bullshit. This was a news articl...      4              0   
499  Does the HunterBiden HunterBidenEmails NYPost ...      0              0   

                 source       user_id           user_name user_screen_name  \
0             TweetDeck  3.606665e+08  El Sol Latino News  elsollatinonews   
1      Twitter for iPad  8.099044e+08   Cheri A. üá∫üá∏     Biloximeemaw   
2       Twitter Web App  3.494182e+09          Flag Waver      Flag_Wavers   
3    Twitter for iPhone  8.240000e+17       Michelle Ferg    MichelleFerg4   
4       Twitter Web App  1.030000e+18      the Gold State    theegoldstate   
..                  ...           ...                 ...              ...   
495  Twitter for iPhone  3.031552e+07          Susan Ward    Susaninlaguna   
496     Twitter Web App  8.256080e+08   Justin T. Haskins   JustinTHaskins   
497     Twitter Web App  9.470000e+17      Nicholas Sones        NickSones   
498  Twitter for iPhone  7.749858e+08              kaytee    TeamDaniMBB14   
499  Twitter for iPhone  1.290000e+18      @realateachick    realateachick   

                                      user_description  ...        lat  \
0    üåê Noticias de inter√©s para latinos de la c...  ...  25.774270   
1    Locked and loaded Meemaw. Love God, my family ...  ...  25.774270   
2    Locked and loaded Meemaw. Love God, my family ...  ...  46.304036   
3    Locked and loaded Meemaw. Love God, my family ...  ...  46.304036   
4    A Silicon Valley #independent #News #Media #St...  ...  36.701463   
..                                                 ...  ...        ...   
495  Amazon Bestselling Author. Believes in family ...  ...  29.949932   
496  Christian. Conservative Millennial. Editorial ...  ...  36.638392   
497        Fight Back Harder! Publisher of @GLRepublic  ...  41.299538   
498  Names Kaytee. 1st Official fan account for the...  ...  41.299538   
499        Reality TV nonsense and nonsense in general  ...  41.737023   

           long              city                   country      continent  \
0    -80.193660               NaN  United States of America  North America   
1    -80.193660               NaN  United States of America  North America   
2   -109.171431               NaN  United States of America  North America   
3   -109.171431               NaN  United States of America  North America   
4   -118.755997               NaN  United States of America  North America   
..          ...               ...                       ...            ...   
495  -90.070116       New Orleans  United States of America  North America   
496  127.696119       New Orleans               South Korea           Asia   
497  -74.848779  Dingman Township  United States of A

In [9]:
tweet_data.columns

Index(['created_at', 'tweet_id', 'tweet', 'likes', 'retweet_count', 'source',
       'user_id', 'user_name', 'user_screen_name', 'user_description',
       'user_join_date', 'user_followers_count', 'user_location', 'lat',
       'long', 'city', 'country', 'continent', 'state', 'state_code',
       'collected_at', 'Polarity_score', 'Sentiment'],
      dtype='object')

In [10]:
sentiment = pd.DataFrame(tweet_data['Sentiment'].value_counts())
sentiment

Sentiment
neutral         249
positive        155
negative         96

In [11]:
tweet_geodata = gpd.GeoDataFrame(tweet_data, geometry=gpd.points_from_xy(x=tweet_data['long'],y=tweet_data['lat']))

In [12]:
tweet_geodata

created_at      tweet_id  \
0    15/10/2020 00:00  1.320000e+18   
1    15/10/2020 00:00  1.320000e+18   
2    15/10/2020 00:00  1.320000e+18   
3    15/10/2020 00:00  1.320000e+18   
4    15/10/2020 00:00  1.320000e+18   
..                ...           ...   
495  15/10/2020 00:29  1.320000e+18   
496  15/10/2020 00:29  1.320000e+18   
497  15/10/2020 00:29  1.320000e+18   
498  15/10/2020 00:29  1.320000e+18   
499  15/10/2020 00:29  1.320000e+18   

                                                 tweet  likes  retweet_count  \
0    Elecciones2020 | En Florida: JoeBiden dice que...      0              0   
1    HunterBiden HunterBidenEmails JoeBiden JoeBide...      0              0   
2       This is how Biden made his ! TrumpIsNotAmer...      0              0   
3     Watching and setting dvr. Let‚Äôs give him bo...      0              0   
4    censorship HunterBiden Biden BidenEmails Biden...      1              0   
..                                                 ...    ...            ...   
495        Must watchüëáüèªBiden family corruption.      35             32   
496  FACTS:  has been accused of sexual assault, ma...     16             10   
497  Hunter Biden won a Nobel Peace Prize, R's try ...      0              0   
498  This is utter bullshit. This was a news articl...      4              0   
499  Does the HunterBiden HunterBidenEmails NYPost ...      0              0   

                 source       user_id           user_name user_screen_name  \
0             TweetDeck  3.606665e+08  El Sol Latino News  elsollatinonews   
1      Twitter for iPad  8.099044e+08   Cheri A. üá∫üá∏     Biloximeemaw   
2       Twitter Web App  3.494182e+09          Flag Waver      Flag_Wavers   
3    Twitter for iPhone  8.240000e+17       Michelle Ferg    MichelleFerg4   
4       Twitter Web App  1.030000e+18      the Gold State    theegoldstate   
..                  ...           ...                 ...              ...   
495  Twitter for iPhone  3.031552e+07          Susan Ward    Susaninlaguna   
496     Twitter Web App  8.256080e+08   Justin T. Haskins   JustinTHaskins   
497     Twitter Web App  9.470000e+17      Nicholas Sones        NickSones   
498  Twitter for iPhone  7.749858e+08              kaytee    TeamDaniMBB14   
499  Twitter for iPhone  1.290000e+18      @realateachick    realateachick   

                                      user_description  ...        long  \
0    üåê Noticias de inter√©s para latinos de la c...  ...  -80.193660   
1    Locked and loaded Meemaw. Love God, my family ...  ...  -80.193660   
2    Locked and loaded Meemaw. Love God, my family ...  ... -109.171431   
3    Locked and loaded Meemaw. Love God, my family ...  ... -109.171431   
4    A Silicon Valley #independent #News #Media #St...  ... -118.755997   
..                                                 ...  ...         ...   
495  Amazon Bestselling Author. Believes in family ...  ...  -90.070116   
496  Christian. Conservative Millennial. Editorial ...  ...  127.696119   
497        Fight Back Harder! Publisher of @GLRepublic  ...  -74.848779   
498  Names Kaytee. 1st Official fan account for the...  ...  -74.848779   
499        Reality TV nonsense and nonsense in general  ...  -99.587382   

                 city                   country      continent         state  \
0                 NaN  United States of America  North America       Florida   
1                 NaN  United States of America  North America       Florida   
2                 NaN  United States of America  North America       Montana   
3                 NaN  United States of America  North America       Montana   
4                 NaN  United States of America  North America    California   
..                ...                       ...            ...           ...   
495       New Orleans  United States of America  North America     Louisiana   
496       New Orleans               South Korea           Asia     Louisiana   
497  Dingman Township  

In [50]:
this_map = folium.Map(location=[20,0], tiles="OpenStreetMap", zoom_start=3)

In [55]:
def plotDot(point):
    '''input: series that contains a numeric named latitude and a numeric named longitude
    this function creates a CircleMarker and adds it to your this_map'''

    folium.Marker(location=[point.lat, point.long],popup=tweet_data['tweet']).add_to(this_map)

#use tweet_data.apply(,axis=1) to "iterate" through every row in your dataframe
tweet_data.apply(plotDot,axis=1)
this_map.fit_bounds(this_map.get_bounds())
this_map